In [2]:
%run -i ../python/common.py
UC_SKIPTERMS=True
%run -i ../python/ln_preamble.py

# UC-SLS Lecture 9 : Assembly : Operations and Data Types

## A simple mov.S program

### Setup

In [3]:
# setup for mov example
movdir=os.getenv('HOME')
movdir=movdir + "/mov"
#print(movdir)
output=runTermCmd("[[ -d " + movdir + " ]] &&  rm -rf "+ movdir + 
             ";mkdir " + movdir + 
             ";cp ../src/mov.S ../src/Makefile ../src/setup.gdb " + movdir)
#TermShellCmd("ls", cwd=movdir)
Markdown('''
- create a directory `mkdir mov; cd mov`
- create and write  `mov.S` below
- add a `Makefile` to automate assembling and linking
    - we are going run the commands by hand this time to highlight the details
- add our `setup.gdb` to make working in gdb easier
- normally you would want to track everything in git
''')


- create a directory `mkdir mov; cd mov`
- create and write  `mov.S` below
- add a `Makefile` to automate assembling and linking
    - we are going run the commands by hand this time to highlight the details
- add our `setup.gdb` to make working in gdb easier
- normally you would want to track everything in git


In [4]:
display(Markdown(FileCodeBox(
    file=movdir+"/mov.S", 
    lang="gas", 
    title="<b>CODE: asm - mov.S",
    h="100%", 
    w="107em"
)))

<b>CODE: asm - mov.S
<div style="width:107em; height:100%; font-size:inherit; overflow: auto;" >


``` gas
	.intel_syntax noprefix
	.text
	
	.equ EXIT_SYSCALL_NR,60
	
	.global _start
	.type _start, @function	
_start:
	mov rax, 0b1000

	mov rax, EXIT_SYSCALL_NR
	mov rdi, 2
	syscall
	
	

```


</div>


### Assemble `mov.S ` into `mov.o`  directly with assembler (as)
- `-a` produce listing to standard out
- we could add `-g` flag to add extra debugger information but lets skip it for now

In [5]:
TermShellCmd("rm mov.o;make DEBUG='' mov.o", prompt='', cwd=movdir)


rm: cannot remove 'mov.o': No such file or directory
as  -a=mov.o.lst mov.S -o mov.o



#### `mov.o` is NOT an executable

In [6]:
TermShellCmd("ls -l mov.o", cwd=movdir, pretext='$ ls -l mov.o', prompt='')

$ ls -l mov.o
-rw-r--r-- 1 jovyan root 752 Nov 10 07:01 mov.o



#### What kind of file is is it?

In [7]:
TermShellCmd("file mov.o", cwd=movdir, pretext='$ file mov.o', prompt='')

$ file mov.o
mov.o: ELF 64-bit LSB relocatable, x86-64, version 1 (SYSV), not stripped



#### Examine Symbol Table

In [8]:
TermShellCmd("objdump -t mov.o", cwd=movdir, pretext='$ objdump -t mov.o', prompt='')

$ objdump -t mov.o

mov.o:     file format elf64-x86-64

SYMBOL TABLE:
0000000000000000 l    d  .text	0000000000000000 .text
0000000000000000 l    d  .data	0000000000000000 .data
0000000000000000 l    d  .bss	0000000000000000 .bss
000000000000003c l       *ABS*	0000000000000000 EXIT_SYSCALL_NR
0000000000000000 g     F .text	0000000000000000 _start





### Link  `mov.o` to produce the binary `mov` with linker (ld)
- we don't really have any other files to link 
- simply need to have linker organize things as per os linker script (use `ld -verbose` to see the script )
  - note the syntax is very cryptic


In [9]:
TermShellCmd("make mov", cwd=movdir, prompt='')


ld -g -Map=mov.map mov.o -o mov



In [10]:
TermShellCmd("ls -l mov",cwd=movdir, pretext='$ ls -l mov', prompt='')

$ ls -l mov
-rwxr-xr-x 1 jovyan root 4712 Nov 10 07:01 mov



In [11]:
TermShellCmd("file mov", cwd=movdir, pretext="$ file mov.o", prompt='')

$ file mov.o
mov: ELF 64-bit LSB executable, x86-64, version 1 (SYSV), statically linked, not stripped



In [12]:
TermShellCmd("objdump -t mov", cwd=movdir, prompt='', pretext='$ objdump -t mov') 

$ objdump -t mov

mov:     file format elf64-x86-64

SYMBOL TABLE:
0000000000401000 l    d  .text	0000000000000000 .text
0000000000000000 l    df *ABS*	0000000000000000 mov.o
000000000000003c l       *ABS*	0000000000000000 EXIT_SYSCALL_NR
0000000000401000 g     F .text	0000000000000000 _start
0000000000402000 g       .text	0000000000000000 __bss_start
0000000000402000 g       .text	0000000000000000 _edata
0000000000402000 g       .text	0000000000000000 _end





In [13]:
TermShellCmd("ld --verbose", cwd=movdir)

$ ld --verbose
GNU ld (GNU Binutils for Ubuntu) 2.34
  Supported emulations:
   elf_x86_64
   elf32_x86_64
   elf_i386
   elf_iamcu
   elf_l1om
   elf_k1om
   i386pep
   i386pe
using internal linker script:
/* Script for -z combreloc -z separate-code */
/* Copyright (C) 2014-2020 Free Software Foundation, Inc.
   Copying and distribution of this script, with or without modification,
   are permitted in any medium without royalty provided the copyright
   notice and this notice are preserved.  */
OUTPUT_FORMAT("elf64-x86-64", "elf64-x86-64",
	      "elf64-x86-64")
OUTPUT_ARCH(i386:x86-64)
ENTRY(_start)
SEARCH_DIR("=/usr/local/lib/x86_64-linux-gnu"); SEARCH_DIR("=/lib/x86_64-linux-gnu"); SEARCH_DIR("=/usr/lib/x86_64-linux-gnu"); SEARCH_DIR("=/usr/lib/x86_64-linux-gnu64"); SEARCH_DIR("=/usr/local/lib64"); SEARCH_DIR("=/lib64"); SEARCH_DIR("=/usr/lib64"); SEARCH_DIR("=/usr/local/lib"); SEARCH_DIR("=/lib"); SEARCH_DIR("=/usr/lib"); SEARCH_DIR("=/usr/x86_64-linux-gnu/lib64"); SEARCH_DIR("=/u

#### recognize anything?

#### lets run it

In [14]:
TermShellCmd("./mov; echo $?", cwd=movdir, prompt='', pretext='$ ./mov\n$ echo $?')

$ ./mov
$ echo $?
2



#### We can use tools to convert the executable into a binary image
- `objcopy` is a very useful tool like `objdump` 
   - let's us convert the executable into various formats including `raw` binary
   - `objcopy mov --output-target=binary mov.bin`

In [15]:
TermShellCmd("objcopy mov --output-target=binary mov.bin", cwd=movdir, prompt='', 
             pretext='objcopy mov --output-target=binary mov.bin')

objcopy mov --output-target=binary mov.bin



In [16]:
TermShellCmd("hexdump -C mov.bin", cwd=movdir, prompt='', 
             pretext='hexdump -C mov.bin')

hexdump -C mov.bin
00000000  48 c7 c0 08 00 00 00 48  c7 c0 3c 00 00 00 48 c7  |H......H..<...H.|
00000010  c7 02 00 00 00 0f 05                              |.......|
00000017



### `gdb -tui mov -x setup.gdb `

#### rebuild with more debug info `-g`

In [17]:
TermShellCmd("make clean; make mov", cwd=movdir, prompt='',pretext='')


rm -f mov mov.o mov.o.lst mov.map
as -g -a=mov.o.lst mov.S -o mov.o
ld -g -Map=mov.map mov.o -o mov



In [18]:

display(showDT(""))

<b>Debug</b>

In [19]:
display(mkImgsAnimateBox(dir="../images/ASSEMBLY-PGMI"))